In [1]:
import pandas as pd
import holoviews as hv
import numpy as np
import json

hv.extension('bokeh', logo = False)

In [3]:

outputfile = '1D_case3.json'
data = json.load( open(outputfile, 'r') )
outputStyle = 'jupyter'

cond = data['condition']
d = data['output']

time = [ p['time'] for p in d ]
distance = [ p['distance'] for p in d[0]['profile'] ]
X = distance 

screenclass =  np.array( cond['screenclass'] )*1000
zb = np.array( cond['elevation'] )
width = np.array( cond['width'] )

def curves(vt, vdis):
    t = time.index(vt)
    x = distance.index(vdis)
    
    dAb = np.array( [ dd['dAb'] for dd in d[t]['profile'] ] )
    dzb = dAb/width
    a = hv.Curve((X, zb + dzb), label='output', kdims='Distance[m]', vdims='Elevation[m]' )
    
    dAb = np.array( [ dd['dAb'] for dd in d[0]['profile'] ] )
    dzb = dAb/width
    b = hv.Curve((X, zb + dzb), label='first')

    c = hv.VLine(float(vdis)).options(color='black',line_width=2, line_dash='dotted')
    
    g1 = hv.Overlay([a,b,c]).relabel('Bed Elevation' ).options(show_grid=True, width=400, legend_position='top_right', show_frame=True)
    
    da = np.array(d[t]['profile'][x]['ratio'])
    da = np.add.accumulate( da )
    da = np.insert(da,0,0)
    a = hv.Curve((screenclass, da), label='output', kdims='daimeter[mm]', vdims='percentage' ).options(logx=True)
    
    da = np.array(d[0]['profile'][x]['ratio'])
    da = np.add.accumulate( da )
    da = np.insert(da,0,0)
    b = hv.Curve((screenclass, da), label='first').options(logx=True)

    g2 = hv.Overlay([a,b]).relabel('grain size distribution').options(show_grid=True, width=300, legend_position='top_left', show_frame=True)
    
    return g1, g2

def curvesdynamic(vt, vdis):
    g1, g2 = curves(vt, vdis)
    return g1 + g2
    
if outputStyle == 'jupyter' :
    dmap = hv.DynamicMap(curvesdynamic, kdims=['time','distance']).options(title_format='')
    out = dmap.redim.values(time=time).redim.values(distance=distance)

elif outputStyle == 'html' : # jupyter
    tp = set(time[::2])
    xp = set(distance[::10])
     
    holo1 = hv.HoloMap(kdims=['time','distance']).options(title_format='')
    holo2 = hv.HoloMap(kdims=['time','distance']).options(title_format='')
    for N in tp :
        for r in xp :
            holo1[(N,r)], holo2[(N,r)] = curves(N, r) 
    
    out = (holo1 + holo2).options(title_format='')

out

:DynamicMap   [time,distance]
   :Layout
      .Overlay.Bed_Elevation           :Overlay
         .Curve.Output :Curve   [Distance[m]]   (Elevation[m])
         .Curve.First  :Curve   [x]   (y)
         .VLine.I      :VLine   [x,y]
      .Overlay.Grain_size_distribution :Overlay
         .Curve.Output :Curve   [daimeter[mm]]   (percentage)
         .Curve.First  :Curve   [x]   (y)